## ** Equipment Failure Analysis **
Pyspark Notebook to supply information within:
* Total equipment failures that happened?
* Which equipment name had most failures?
* Average amount of failures across equipment group, ordered by the number of failures in ascending order?
* Rank the sensors which present the most number of errors by equipment name in an equipment group.

#### notes:
| information | data | notes |
|-------------|:-----------:|------------:|
| Dataset used | 'equipment_sensors.csv', 'equipment.parquet' and 'equpment_failure_sensors.txt' | None |
| Data paths | update path variables in order to work correctly. | None |
| 



#### Environment Setup
<a id="environment_setup"></a>

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import regexp_extract
import os
from datetime import datetime
import logging


spark = SparkSession.builder \
    .appName("Equipment Failure Analysis") \
    .config("spark.some.config.option", "some-value") \
    .enableHiveSupport() \
    .getOrCreate()

# Configuração do Logger para registrar informações
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger("Equipment Failure Analysis")

# Formatação do nome do arquivo com timestamp
timestamp = datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
log_dir = "dbfs/FileStore/shared_uploads/mbarbugli@gmail.com"
log_filename = f"{log_dir}/total_falhas_{timestamp}.txt"

logger = logging.getLogger(f"{timestamp} [INFO] Equipment Failure Analysis - Inacializando...")
logger.info(f"{timestamp} [INFO] Sessão Spark iniciada.")

# Ler os dados
df_sensors = spark.read.csv("dbfs:/FileStore/equipment_sensors.csv", header=True, inferSchema=True)
df_equipment = spark.read.parquet("dbfs:/FileStore/equipment.parquet")
df_logs = spark.read.option("delimiter", "\t").csv("dbfs:/FileStore/equpment_failure_sensors.txt", header=False, inferSchema=True)

logger.info(f"{timestamp} [INFO] Os dados foram carregados com sucesso!")
logger.info(f"{timestamp} [INFO] Atualizando Schema: {df_logs}")

# Schema
df_logs = df_logs.toDF("date", "status", "raw_sensor_data", "temperature", "vibration", "signal")
df_logs = df_logs.withColumn(
    "sensor_id", 
    regexp_extract("raw_sensor_data", r"sensor\[(\d+)\]:", 1)
)
# df_logs = df_logs.join(df_sensors, "sensor_id").join(df_equipment, "equipment_id")
logger.info(f"{timestamp} [UPDATE] O Schema: {df_logs}, foi atualizado com sucesso!")

# logger.info(f"{timestamp} [INFO] Criando tabelas permanentes no metastore...")
# # Criar tabelas permanentes no metastore
# df_sensors.write.saveAsTable("sensors")
# df_equipment.write.saveAsTable("equipment")
# df_logs.write.format("csv").option("header", "false").saveAsTable("logs")
# logger.info(f"{timestamp} [INFO] Tabelas criadas com sucesso!")

log_file_path = f"dbfs:/FileStore/log_{timestamp}_equipment_failure.txt"  # TODO! Atualizar caminho.
# Escrevendo no arquivo de log
try:
    with open(log_file_path, 'w') as file:
        logger.info(f"{timestamp} [INFO] Dados dos logs salvos em {log_file_path}") 
except Exception as e:
    logger.error(f"{timestamp} [ERROR] {e}. LOG FILE WAS NOT CREATED! Please check!")

# Criando Alias
df_logs_alias = df_logs.alias("logs")
df_sensors_alias = df_sensors.alias("sensors")
df_equipment_alias = df_equipment.alias("equipment")

logger.info(f"{timestamp} [INFO] Environment Setup finalizado com sucesso!")

# display - TODO:
display(df_sensors)
display(df_equipment)
display(df_logs)

2024-04-22 23:57:55,000 - INFO - 2024-04-22_23-57-54 [INFO] Sessão Spark iniciada.
2024-04-22 23:58:09,313 - INFO - 2024-04-22_23-57-54 [INFO] Os dados foram carregados com sucesso!
2024-04-22 23:58:09,316 - INFO - 2024-04-22_23-57-54 [INFO] Atualizando Schema: DataFrame[_c0: string, _c1: string, _c2: string, _c3: string, _c4: string, _c5: string]
2024-04-22 23:58:09,357 - INFO - 2024-04-22_23-57-54 [UPDATE] O Schema: DataFrame[date: string, status: string, raw_sensor_data: string, temperature: string, vibration: string, signal: string, sensor_id: string], foi atualizado com sucesso!
2024-04-22 23:58:09,359 - ERROR - 2024-04-22_23-57-54 [ERROR] [Errno 2] No such file or directory: 'dbfs:/FileStore/log_2024-04-22_23-57-54_equipment_failure.txt'. LOG FILE WAS NOT CREATED! Please check!
2024-04-22 23:58:09,366 - INFO - 2024-04-22_23-57-54 [INFO] Environment Setup finalizado com sucesso!


equipment_id sensor_id 1 4275 2 5212 3 7381 4 396 5 1645 6 9532 7 3328 8 8461 9 2173 10 3499 11 8551 12 3965 13 8271 14 2768 1 8725 2 3167 3 6078 4 7001 5 5477 6 2278 7 232 8 5857 9 4938 10 7890 11 1203 12 9624 13 4223 14 1797 1 5627 2 4957 3 1073 4 2823 5 4814 6 4125 7 7570 8 1213 9 2314 10 570 11 6238 12 6789 13 8103 14 6598 1 4093 2 2191 3 2006 4 2588 5 3588 6 8500 7 5948 8 3867 9 8812 10 1476 11 2679 12 3297 13 9974 14 2295 1 3193 2 1088 3 6439 4 2440 5 7064 6 4356 7 9036 8 3891 9 2609 10 5691 11 1020 12 6142 13 4395 14 2906 1 9286 2 4466 3 6658 4 285 5 3689 6 7122 7 2777 8 5255 9 3451 10 9652 11 4630 12 5245 13 9493 14 4697 1 8738 2 6502 3 9812 4 1383 5 8768 6 1102 7 7312 8 8907 9 7451 10 441 11 4214 12 4449 13 9129 14 1843 1 388 2 8150 3 827 4 4027 5 4031 6 6938 7 5612 8 4160 9 3016 10 7086 11 5799 12 7442 13 655 14 7624 1 2016 2 9019 3 4340 4 7556 5 207 6 4320 7 8564 8 5587 9 1820 10 6586 11 9975 12 6029 13 8309 14 8761 1 3029 2 9686 3 3168 4 3032 5 3257 6 1111 7 1679 8 5243 9 4336 10 1781 11 2079 12 3980 13 3705 14 126 1 8726 2 2154 3 2894 4 1564 5 4759 6 4209 7 2303 8 3442 9 4968 10 9422 11 4700 12 3226 13 8403 14 4200 1 5396 2 2216 3 8612 4 5877 5 5004 6 7237 7 6964 8 5876 9 694 10 4555 11 4297 12 5793 13 8436 14 2087 1 751 2 8211 3 5821 4 115 5 6180 6 9 7 2582 8 9720 9 9031 10 6561 11 4237 12 4955 13 4703 14 2943 1 6670 2 1099 3 4083 4 6476 5 5993 6 3789 7 9423 8 8227 9 836 10 9261 11 6740 12 5839 13 3701 14 3773 1 3143 2 6668 3 9670 4 4490 5 6892 6 7671 7 1638 8 4470 9 1508 10 380 11 1201 12 1261 13 7104 14 4041 1 5513 2 4078 3 1392 4 3060 5 9362 6 9922 7 5197 8 332 9 9055 10 1726 11 3097 12 1514 13 1758 14 5459 1 2431 2 5918 3 7769 4 7040 5 7503 6 2203 7 4967 8 4061 9 6043 10 7388 11 5356 12 7254 13 9373 14 2445 1 5713 2 4184 3 8012 4 5561 5 4881 6 7161 7 8559 8 7919 9 4441 10 3068 11 8021 12 2937 13 249 14 1551 1 950 2 5796 3 1534 4 8453 5 6130 6 796 7 7356 8 1945 9 6653 10 5097 11 5176 12 5595 13 2804 14 4068 1 8441 2 3649 3 631 4 7949 5 2309 6 4914 7 3269 8 832 9 7717 10 5456 11 2367 12 9564 13 6487 14 9622 1 2729 2 1044 3 1863 4 1747 5 356 6 7557 7 3528 8 8900 9 469 10 9462 11 9253 12 3817 13 2984 14 9181 1 5276 2 846 3 1363 4 2936 5 9448 6 4509 7 4398 8 8357 9 7582 10 9093 11 3563 12 2294 13 513 14 7435 1 5804 2 1162 3 8079 4 8057 5 2599 6 4058 7 3576 8 8758 9 1262 10 3511 11 9958 12 5204 13 4979 14 9119 1 8351 2 9078 3 714 4 2558 5 5782 6 5515 7 9582 8 9497 9 7342 10 2654 11 8687 12 6505 13 2172 14 428 1 5009 2 3107 3 9793 4 562 5 4956 6 2161 7 9847 8 4047 9 8836 10 7298 11 683 12 7673 13 6974 14 3245 1 8157 2 5929 3 5372 4 9366 5 5117 6 2184 7 8486 8 3506 9 8911 10 5318 11 2949 12 7406 13 6639 14 120 1 7175 2 9769 3 2618 4 165 5 8275 6 689 7 8198 8 6394 9 7181 10 8533 11 7927 12 3276 13 8030 14 660 1 7412 2 7480 3 3963 4 7522 5 3480 6 9990 7 7677 8 8418 9 7415 10 5277 11 1892 12 3487 13 447 14 1946 1 6756 2 3580 3 999 4 3150 5 2933 6 776 7 6855 8 8159 9 1251 10 9729 11 2299 12 1274 13 6806 14 875 1 9345 2 682 3 2697 4 8189 5 5177 6 4458 7 5434 8 5315 9 1609 10 4844 11 291 12 2137 13 1306 14 2668 1 717 2 7234 3 9804 4 9750 5 5451 6 7386 7 4577 8 4590 9 4565 10 8117 11 8390 12 4217 13 7285 14 9530 1 8365 2 9406 3 8823 4 6631 5 2213 6 8155 7 5091 8 2846 9 4646 10 6294 11 9725 12 5413 13 7284 14 7842 1 7141 2 666 3 5707 4 1317 5 964 6 79 7 4283 8 697 9 6540 10 262 11 6260 12 3235 13 5490 14 7604 1 4249 2 1152 3 1023 4 3387 5 6935 6 2407 7 1395 8 335 9 6638 10 7797 11 7643 12 4621 13 9708 14 7289 1 7067 2 3509 3 8473 4 1876 5 8349 6 364 7 8729 8 9309 9 5620 10 267 11 6415 12 6108 13 4906 14 9940 1 6116 2 3882 3 3758 4 3485 5 6160 6 3307 7 7010 8 2565 9 2803 10 6438 11 5102 12 1506 13 4850 14 4768 1 1741 2 6532 3 9335 4 2806 5 8502 6 7978 7 9240 8 5480 9 7854 10 7416 11 7259 12 3195 13 1405 14 9327 1 7165 2 8951 3 7367 4 8800 5 5837 6 5954 7 7784 8 6588 9 9341 10 6567 11 5184 12 2257 13 5842 14 6320 1 1459 2 3717 3 3398 4 5514 5 6845 6 28 7 2709 8 6991 9 2749 10 133 11 4720 12 5664 13 1074 14 7686 1 3352 2 9680 3

equipment_id name group_name 1 5310B9D7 FGHQWR2Q 2 43B81579 VAPQY59S 3 E1AD07D4 FGHQWR2Q 4 ADE40E7F 9N127Z5P 5 78FFAD0C 9N127Z5P 6 9AD15F7E PA92NCXZ 7 E54B5C3A FGHQWR2Q 8 86083278 NQWPA8D3 9 3329175B VAPQY59S 10 98B84035 NQWPA8D3 11 09C37FB8 PA92NCXZ 12 CF304D24 FGHQWR2Q 13 4E834E81 Z9K1SAP4 14 2C195700 VAPQY59S

date status raw_sensor_data temperature vibration signal sensor_id [2021-05-18 0:20:48] ERROR sensor[5820]: (temperature 311.29, vibration 6749.50) 5820 [2021-05-18 0:20:48] ERROR sensor[5820]: (temperature 311.29, vibration 6749.50) 5820 [2021-06-14 19:46:9] ERROR sensor[3359]: (temperature 270.00, vibration -335.39) 3359 [2020-09-27 22:55:11] ERROR sensor[9503]: (temperature 255.84, vibration 1264.54) 9503 [2019-02-9 20:56:4] ERROR sensor[3437]: (temperature 466.57, vibration -1865.26) 3437 [2019-02-6 6:19:34] ERROR sensor[2958]: (temperature 143.02, vibration -4993.13) 2958 [2019-08-10 20:23:22] ERROR sensor[3743]: (temperature 249.81, vibration 8925.85) 3743 [2021-03-25 14:39:49] ERROR sensor[6282]: (temperature 475.57, vibration -2859.46) 6282 [2020-05-15 17:30:17] ERROR sensor[2477]: (temperature 200.20, vibration -6866.76) 2477 [2020-12-11 11:52:47] ERROR sensor[3838]: (temperature 330.33, vibration -6170.30) 3838 [2019-04-16 8:28:34] ERROR sensor[4031]: (temperature 310.94, vibration 7200.50) 4031 [2020-10-1 20:8:30] ERROR sensor[6848]: (temperature 495.47, vibration 7626.35) 6848 [2019-03-13 4:13:22] ERROR sensor[1633]: (temperature 124.81, vibration -5077.34) 1633 [2020-01-11 11:43:48] ERROR sensor[7474]: (temperature 335.82, vibration 9551.73) 7474 [2020-02-9 13:57:55] ERROR sensor[6229]: (temperature 499.29, vibration 7891.62) 6229 [2020-04-22 18:30:7] ERROR sensor[2722]: (temperature 325.49, vibration 4127.27) 2722 [2021-03-27 19:56:16] ERROR sensor[2163]: (temperature 465.82, vibration -6645.87) 2163 [2020-06-3 9:37:17] ERROR sensor[8816]: (temperature 117.71, vibration -1004.52) 8816 [2019-08-22 5:1:4] ERROR sensor[4329]: (temperature 97.47, vibration -6519.88) 4329 [2021-02-10 6:0:19] ERROR sensor[258]: (temperature 222.88, vibration err) 258 [2020-02-10 13:7:46] ERROR sensor[6210]: (temperature 463.73, vibration 4560.12) 6210 [2019-09-10 17:47:27] ERROR sensor[4784]: (temperature 146.91, vibration -1252.38) 4784 [2019-05-16 5:8:20] ERROR sensor[6743]: (temperature 223.54, vibration -7383.11) 6743 [2021-07-23 10:30:29] ERROR sensor[6265]: (temperature 450.93, vibration -7194.56) 6265 [2021-04-11 0:51:11] ERROR sensor[6356]: (temperature 368.22, vibration 3363.96) 6356 [2019-03-27 4:52:31] ERROR sensor[2508]: (temperature 381.15, vibration -9950.29) 2508 [2019/02/17] WARNING sensor[9001]: (temperature 467.62, vibration 6162.13) 9001 [2019-10-23 9:54:34] ERROR sensor[8685]: (temperature 186.49, vibration -7842.91) 8685 [2019-09-17 15:2:48] ERROR sensor[3653]: (temperature 6.43, vibration -3741.38) 3653 [2020-02-14 2:44:10] ERROR sensor[7965]: (temperature 80.49, vibration 1009.49) 7965 [2019-06-19 19:18:27] ERROR sensor[558]: (temperature 111.65, vibration -336.23) 558 [2020-10-18 16:24:35] ERROR sensor[3963]: (temperature 259.83, vibration -1592.77) 3963 [2020-07-2 8:46:21] ERROR sensor[8138]: (temperature 200.33, vibration -2670.17) 8138 [2019-02-7 1:10:33] ERROR sensor[8912]: (temperature 424.33, vibration 6141.48) 8912 [2019-11-5 11:45:46] ERROR sensor[5140]: (temperature 401.99, vibration -128.38) 5140 [2019-08-28 18:27:45] ERROR sensor[4040]: (temperature 251.97, vibration 9954.87) 4040 [2019-08-7 14:25:26] ERROR sensor[5608]: (temperature 121.28, vibration -6875.62) 5608 [2021-02-4 6:21:17] ERROR sensor[6041]: (temperature 32.23, vibration 6830.55) 6041 [2019-10-9 15:42:11] ERROR sensor[1255]: (temperature 491.52, vibration -3999.35) 1255 [2020-10-7 20:15:31] ERROR sensor[5801]: (temperature 110.80, vibration err) 5801 [2020-05-13 22:26:57] ERROR sensor[4308]: (temperature 431.32, vibration err) 4308 [2019-06-2 14:29:46] ERROR sensor[2443]: (temperature 297.79, vibration -6938.60) 2443 [2019-04-9 10:49:21] ERROR sensor[2524]: (temperature 112.62, vibration -1916.82) 2524 [2019-04-7 2:14:48] ERROR sensor[1268]: (temperature 442.03, vibration -8816.09) 1268 [2019-06-11 21:44:36] ERROR sensor[774]: (temperature 87.12, vibration 920.54) 774 [2019-03-2 8:22:59] ERROR sensor[1199]: (temperature 317.99, vibration

### ErrorLogAnalysis
<a id2="ErrorLogAnalysis"></a>

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col

spark = SparkSession.builder.appName("ErrorLogAnalysis").getOrCreate()

# Log inicial
logger.info(f"{timestamp} [INFO] Equipment Failure Analysis - Inciando o 'ErrorLogAnalysis'")
logger.info(f"{timestamp} [INFO] Criando tabelas: 'failures_with_equipment' e 'equipment_failure_counts'...") 

# Join
failures_with_equipment = df_logs_alias \
    .join(df_sensors_alias, df_logs_alias["sensor_id"] == df_sensors_alias["sensor_id"]) \
    .join(df_equipment_alias, df_sensors_alias["equipment_id"] == df_equipment_alias["equipment_id"])

logger.info(f"{timestamp} [INFO] Ação realizada com sucesso!") 
logger.info(f"{timestamp} [INFO] Inciando Transformação de dados: ErrorLogAnalysis ") 

# Filtrar apenas linhas com 'status' igual a 'ERROR'
failures_with_equipment = failures_with_equipment.filter(col("status") == "ERROR")

# 'count' na coluna 'name' from dataframe 'equipment'
equipment_failure_counts = failures_with_equipment \
    .groupBy(df_equipment_alias["name"]) \
    .count() \
    .orderBy(col("count").desc())

# Criando dataframe equipment_failure_counts
equipment_failure_counts = equipment_failure_counts \
    .withColumnRenamed("name", "equipment_name") \
    .withColumnRenamed("count", "equipment_failure_count")
most_failures_equipment = equipment_failure_counts.first()
logger.info(f"{timestamp} [WARNING] Equipamento com maior numero de falhas: {most_failures_equipment} ") 

# Salvando a tabela no databricks.
logger.info(f"{timestamp} [INFO] Salvando tabelas: {equipment_failure_counts}...") 
equipment_failure_counts.write.option("overwriteSchema", "true").format("delta").mode("overwrite").saveAsTable("most_failures_equipment")
logger.info(f"{timestamp} [INFO] Ação realizada com sucesso!") 
display(equipment_failure_counts)
logger.info(f"{timestamp} [INFO] ErrorLogAnalysis - Finalizado com sucesso!") 


2024-04-22 23:58:10,896 - INFO - 2024-04-22_23-57-54 [INFO] Equipment Failure Analysis - Inciando o 'ErrorLogAnalysis'
2024-04-22 23:58:10,898 - INFO - 2024-04-22_23-57-54 [INFO] Criando tabelas: 'failures_with_equipment' e 'equipment_failure_counts'...
2024-04-22 23:58:10,944 - INFO - 2024-04-22_23-57-54 [INFO] Ação realizada com sucesso!
2024-04-22 23:58:10,946 - INFO - 2024-04-22_23-57-54 [INFO] Inciando Transformação de dados: ErrorLogAnalysis 
2024-04-22 23:58:31,086 - INFO - 2024-04-22_23-57-54 [WARNING] Equipamento com maior numero de falhas: Row(equipment_name='2C195700', equipment_failure_count=343800) 
2024-04-22 23:58:31,102 - INFO - 2024-04-22_23-57-54 [INFO] Salvando tabelas: DataFrame[equipment_name: string, equipment_failure_count: bigint]...
2024-04-22 23:58:56,661 - INFO - 2024-04-22_23-57-54 [INFO] Ação realizada com sucesso!


equipment_name equipment_failure_count 2C195700 343800 9AD15F7E 343526 98B84035 342870 78FFAD0C 341033 4E834E81 340549 43B81579 340188 E1AD07D4 340169 ADE40E7F 339698 3329175B 339561 86083278 338766 5310B9D7 337033 CF304D24 334843 09C37FB8 334615 E54B5C3A 332824

2024-04-22 23:59:17,080 - INFO - 2024-04-22_23-57-54 [INFO] ErrorLogAnalysis - Finalizado com sucesso!


### Equipment with Most Failures
<a id4="equipment_most_failures"></a>

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col

spark = SparkSession.builder.appName("EquipmentWithMostFailures").getOrCreate()


logger.info(f"{timestamp} [INFO] Iniciando Transformação de dados: Equipment with Most Failures ") 
equipment_failures = equipment_failure_counts.groupBy("equipment_name").count()
most_failures = equipment_failures.orderBy(col("count").desc()).limit(1)

# Extrair o nome do equipamento com o maior número de falhas (em lista)
most_failures_collect = most_failures.collect() 
if most_failures_collect:
    most_failures_row = most_failures_collect[0] 
    equipment_with_most_failures = most_failures_row["equipment_name"]
    logger.info(f"{timestamp} [INFO] Equipamento com maior número de falha: {equipment_with_most_failures}")
else:
    logger.info(f"{timestamp} [INFO] Nenhum dado encontrado para equipamentos com falhas.")

# Verifica se 'most_failures_collect' é uma lista e transforma em dataframe
if isinstance(most_failures_collect, list):
    most_failures_collect = spark.createDataFrame(most_failures_collect)

# Salvando a tabela no databricks.
logger.info(f"{timestamp} [INFO] Criando tabelas: 'most_failures_collect'...") 
most_failures_collect.write.option("overwriteSchema", "true").format("delta").mode("overwrite").saveAsTable("most_failures_collect")
display(most_failures)
logger.info(f"{timestamp} [INFO] Ação realizada com sucesso!")
logger.info(f"{timestamp} [INFO] Equipment with Most Failures - Finalizado com sucesso!") 



2024-04-22 23:59:17,213 - INFO - 2024-04-22_23-57-54 [INFO] Iniciando Transformação de dados: Equipment with Most Failures 
2024-04-22 23:59:37,559 - INFO - 2024-04-22_23-57-54 [INFO] Equipamento com maior número de falha: 2C195700
2024-04-22 23:59:37,806 - INFO - 2024-04-22_23-57-54 [INFO] Criando tabelas: 'most_failures_collect'...


equipment_name count 2C195700 1

2024-04-23 00:00:03,805 - INFO - 2024-04-22_23-57-54 [INFO] Ação realizada com sucesso!
2024-04-23 00:00:03,806 - INFO - 2024-04-22_23-57-54 [INFO] Equipment with Most Failures - Finalizado com sucesso!


### Average Failures by Equipment Group
<a id5="average_group"></a>

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window

logger.info(f"{timestamp} [INFO] Inciando Transformação de dados: Average Failures by Equipment Group") 
logger.info(f"{timestamp} [INFO] Criando DataFrame...")

# Criação de dataframes
failures_with_equipment = df_logs_alias.join(
    df_sensors_alias,
    df_logs_alias["sensor_id"] == df_sensors_alias["sensor_id"],
    "inner"
).join(
    df_equipment_alias,
    df_sensors_alias["equipment_id"] == df_equipment_alias["equipment_id"],
    "inner"
)
logger.info(f"{timestamp} [INFO] DataFrame criado com sucesso!") 

# Calculo da media de falhas por Grupo de Equipamento 
logger.info(f"{timestamp} [INFO] Inciando o calculo da media de falhas por Grupo de Equipamento") 
equipment_failure_counts = failures_with_equipment.groupBy(
    df_equipment_alias["equipment_id"].alias("equipment_id"),
    "group_name"
).agg(
    F.count("status").alias("equipment_failure_count")
)

# Calculo total de falhas entre todos os grupos
windowSpec = Window.partitionBy()  # Sem partition
total_failures = F.sum("equipment_failure_count").over(windowSpec)

# Calculo da porcengatem do total de falhas por grupo e criando coluna
equipment_failure_counts = equipment_failure_counts.withColumn(
    "failure_percent",
    F.col("equipment_failure_count") / total_failures * 100
)

# Calculo média por 'group_name'
avg_failures_per_group = equipment_failure_counts.groupBy("group_name").agg(
    F.avg("equipment_failure_count").alias("avg_failures"),
    F.avg("failure_percent").alias("avg_failure_percent")
)

# Ordenando por "'avg_failures' descending" para encontrar grupo com maior numero de falhas
avg_failures_per_group = avg_failures_per_group.orderBy(F.desc("avg_failures"))

# Salvando a tabela no databricks
logger.info(f"{timestamp} [INFO] Criando tabelas: 'avg_failures_per_group'...") 
avg_failures_per_group.write.option("overwriteSchema", "true").format("delta").mode("overwrite").saveAsTable("most_failureavg_failures_per_groups_collect")
display(avg_failures_per_group)
logger.info(f"{timestamp} [INFO] Ação realizada com sucesso!")
logger.info(f"{timestamp} [INFO] Average Failures by Equipment Group - Finalizado com sucesso!") 

2024-04-23 00:00:03,986 - INFO - 2024-04-22_23-57-54 [INFO] Inciando Transformação de dados: Average Failures by Equipment Group
2024-04-23 00:00:03,991 - INFO - 2024-04-22_23-57-54 [INFO] Criando DataFrame...
2024-04-23 00:00:04,039 - INFO - 2024-04-22_23-57-54 [INFO] DataFrame criado com sucesso!
2024-04-23 00:00:04,041 - INFO - 2024-04-22_23-57-54 [INFO] Inciando o calculo da media de falhas por Grupo de Equipamento
2024-04-23 00:00:04,654 - INFO - 2024-04-22_23-57-54 [INFO] Criando tabelas: 'avg_failures_per_group'...


group_name avg_failures avg_failure_percent NQWPA8D3 357634.5 7.152688569462287 9N127Z5P 357569.5 7.151388569722286 Z9K1SAP4 357528.0 7.150558569888286 VAPQY59S 356937.0 7.138738572252286 PA92NCXZ 356892.5 7.137848572430286 FGHQWR2Q 356867.25 7.137343572531286

2024-04-23 00:00:50,780 - INFO - 2024-04-22_23-57-54 [INFO] Ação realizada com sucesso!
2024-04-23 00:00:50,782 - INFO - 2024-04-22_23-57-54 [INFO] Average Failures by Equipment Group - Finalizado com sucesso!


### CSV
<a id6="csv"></a>

In [0]:
# Importar a sessão Spark
from pyspark.sql import SparkSession

logger.info(f"{timestamp} [INFO] Salvando Resultado em CSV: Inicializando...") 
logger.info(f"{timestamp} [INFO] Criando DataFrame...")
df1 = spark.table("most_failures_equipment")
df2 = spark.table("most_failures_collect")
df3 = spark.table("most_failureavg_failures_per_groups_collect")
logger.info(f"{timestamp} [INFO] Ação realizada com sucesso!")

# DBFS (Databricks File System) onde o arquivo CSV será salvo
output_path1 = f"dbfs:/FileStore/most_failures_equipment_{timestamp}.csv"
output_path2 = f"dbfs:/FileStore/most_failures_collect_{timestamp}.csv"
output_path3 = f"dbfs:/FileStore/avg_failures_per_group_{timestamp}.csv"
logger.info(f"{timestamp} [INFO] Salvado CSV: {output_path1}, {output_path2}, {output_path3}")

# Salvar o DataFrame como CSV
df1.write.csv(path=output_path1, mode="overwrite", header=True)
df2.write.csv(path=output_path2, mode="overwrite", header=True)
df3.write.csv(path=output_path3, mode="overwrite", header=True)
logger.info(f"{timestamp} [INFO] Ação realizada com sucesso!")

logger.info(f"{timestamp} [INFO] CSV Saving - Finalizado com sucesso!") 

# Finalizando programa
logger.info(f"{timestamp} [INFO] Finalizando o Equipment Failure - Tech Case") 
logger.info(f"{timestamp} [INFO] Finalizando logs") 


2024-04-23 00:00:50,933 - INFO - 2024-04-22_23-57-54 [INFO] Salvando Resultado em CSV: Inicializando...
2024-04-23 00:00:50,935 - INFO - 2024-04-22_23-57-54 [INFO] Criando DataFrame...
2024-04-23 00:00:51,309 - INFO - 2024-04-22_23-57-54 [INFO] Ação realizada com sucesso!
2024-04-23 00:00:51,313 - INFO - 2024-04-22_23-57-54 [INFO] Salvado CSV: dbfs:/FileStore/most_failures_equipment_2024-04-22_23-57-54.csv, dbfs:/FileStore/most_failures_collect_2024-04-22_23-57-54.csv, dbfs:/FileStore/avg_failures_per_group_2024-04-22_23-57-54.csv
2024-04-23 00:00:55,939 - INFO - 2024-04-22_23-57-54 [INFO] Ação realizada com sucesso!
2024-04-23 00:00:55,941 - INFO - 2024-04-22_23-57-54 [INFO] CSV Saving - Finalizado com sucesso!
2024-04-23 00:00:55,942 - INFO - 2024-04-22_23-57-54 [INFO] Finalizando o Equipment Failure - Tech Case
2024-04-23 00:00:55,944 - INFO - 2024-04-22_23-57-54 [INFO] Finalizando logs
